In [1]:
!git clone -b llama4 https://github.com/kIshizaki-sci/AutoAWQ.git
!pip install -e ./AutoAWQ
!pip install -U transformers

Cloning into 'AutoAWQ'...
remote: Enumerating objects: 3588, done.
remote: Counting objects: 100% (842/842), done.
remote: Compressing objects: 100% (303/303), done.
remote: Total 3588 (delta 724), reused 561 (delta 539), pack-reused 2746 (from 3)
Receiving objects: 100% (3588/3588), 7.16 MiB | 29.69 MiB/s, done.
Resolving deltas: 100% (2276/2276), done.
Obtaining file:///workspace/AutoAWQ
  Preparing metadata (setup.py) ... done
  Attempting uninstall: autoawq
    Found existing installation: autoawq 0.2.7.post3
    Uninstalling autoawq-0.2.7.post3:
      Successfully uninstalled autoawq-0.2.7.post3
  DEPRECATION: Legacy editable install of autoawq==0.2.8 from file:///workspace/AutoAWQ (setup.py develop) is deprecated. pip 25.0 will enforce this behaviour change. A possible replacement is to add a pyproject.toml or enable --use-pep517, and use setuptools >= 64. If the resulting installation is not behaving as expected, try using --config-settings editable_mode=compat. Please consult t

In [1]:
from awq import AutoAWQForCausalLM
import torch
import transformers
from transformers import AutoProcessor

In [2]:
print('torch version : ', torch.__version__)
print('transformers version : ', transformers.__version__)

torch version :  2.4.1+cu124
transformers version :  4.51.3


In [3]:
quant_path = 'kishizaki-sci/Llama-4-Scout-17B-16E-Instruct-AWQ'

In [4]:
%%time
model = AutoAWQForCausalLM.from_quantized(quant_path, torch_dtype=torch.float16, use_cache=True, device_map='auto')
processor = AutoProcessor.from_pretrained(quant_path)

/workspace/AutoAWQ/awq/models/llama4.py:312: UserWarning: Multimodal input has not been implemented in Llama4AWQForConditionalGeneration yet.
  warnings.warn("Multimodal input has not been implemented in Llama4AWQForConditionalGeneration yet.", UserWarning)


Fetching 25 files:   0%|          | 0/25 [00:00<?, ?it/s]

Replacing MoE Block...:   0%|          | 0/48 [00:00<?, ?it/s]

Replacing layers...: 100%|██████████| 48/48 [00:08<00:00,  5.64it/s]
/workspace/AutoAWQ/awq/models/base.py:539: UserWarning: Skipping fusing modules because AWQ extension is not installed.No module named 'awq_ext'
  warnings.warn("Skipping fusing modules because AWQ extension is not installed." + msg)


CPU times: user 1h 44min 10s, sys: 24min 2s, total: 2h 8min 12s
Wall time: 22min 57s


In [5]:
!nvidia-smi

Fri May  2 23:45:15 2025       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 570.86.15              Driver Version: 570.86.15      CUDA Version: 12.8     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA H100 NVL                On  |   00000000:C7:00.0 Off |                    0 |
| N/A   36C    P0             92W /  310W |   60518MiB /  95830MiB |      0%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+-----

In [6]:
url1 = "https://huggingface.co/datasets/huggingface/documentation-images/resolve/0052a70beed5bf71b92610a43a52df6d286cd5f3/diffusers/rabbit.jpg"
url2 = "https://huggingface.co/datasets/huggingface/documentation-images/resolve/main/datasets/cat_style_layout.png"
messages = [
    {
        "role": "user",
        "content": [
            {"type": "image", "url": url1},
            {"type": "image", "url": url2},
            {"type": "text", "text": "Can you describe how these two images are similar, and how they differ?"},
        ]
    },
]

In [7]:
inputs = processor.apply_chat_template(
    messages,
    add_generation_prompt=True,
    tokenize=True,
    return_dict=True,
    return_tensors="pt",
).to(model.model.device, torch.float16)

In [8]:
%%time
outputs = model.generate(
    **inputs,
    max_new_tokens=256,
)

CPU times: user 59.6 s, sys: 3.29 s, total: 1min 2s
Wall time: 1min 2s


In [9]:
response = processor.batch_decode(outputs[:, inputs["input_ids"].shape[-1]:])[0]
print(response)

The two images depict anthropomorphic animals, a rabbit and a cat, dressed in formal attire. The similarities between the images include:

*   **Formal Attire**: Both characters wear formal clothing, with the rabbit dressed in a blue coat, brown vest, white shirt, and brown bow tie, while the cat wears a similar outfit consisting of a blue jacket, tan vest, white shirt, and red bow tie.
*   **Anthropomorphic Features**: Both characters have human-like features such as standing on two legs (rabbit) or sitting upright (cat), and wearing clothes like humans.
*   **Natural Setting**: Both images are set in a natural environment, with the rabbit standing on a dirt path surrounded by flowers and trees, and the cat sitting on a stone path in a garden-like setting.

Despite these similarities, there are also some notable differences:

*   **Species**: The most obvious difference is that one character is a rabbit and the other is a cat.
*   **Posture**: The rabbit stands upright on two legs, wh